## data

In [2]:
import pandas as pd

# 数据读取
data = pd.read_csv('./AI_Human.csv')
data


C:\Users\ASUS\AppData\Roaming\Python\Python311\site-packages\pandas\core\arrays\masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


text  generated
0       Cars. Cars have been around since they became ...        0.0
1       Transportation is a large necessity in most co...        0.0
2       "America's love affair with it's vehicles seem...        0.0
3       How often do you ride in a car? Do you drive a...        0.0
4       Cars are a wonderful thing. They are perhaps o...        0.0
...                                                   ...        ...
487230  Tie Face on Mars is really just a big misunder...        0.0
487231  The whole purpose of democracy is to create a ...        0.0
487232  I firmly believe that governments worldwide sh...        1.0
487233  I DFN't agree with this decision because a LFT...        0.0
487234  Richard Non, Jimmy Carter, and Bob Dole and ot...        0.0

[487235 rows x 2 columns]

In [3]:
import json
# 提取人类文本 (generated=0.0)
human_texts = data[data['generated'] == 0.0]['text'].tolist()

# 提取 AI 文本 (generated=1.0)
ai_texts = data[data['generated'] == 1.0]['text'].tolist()

# 保存为 JSON 文件
with open('human.json', 'w', encoding='utf-8') as f:
    json.dump(human_texts, f, ensure_ascii=False, indent=4)

with open('AI.json', 'w', encoding='utf-8') as f:
    json.dump(ai_texts, f, ensure_ascii=False, indent=4)

print("人类文本数量:", len(human_texts))
print("AI 生成文本数量:", len(ai_texts))

人类文本数量: 305797
AI 生成文本数量: 181438


## rewrite

In [3]:
import json
import random
from openai import OpenAI
from tenacity import retry, stop_after_attempt, wait_random_exponential

# ✅ 初始化 DeepSeek API 客户端
client = OpenAI(
    api_key="sk-02f85c18644c4cabbcad55f0961122f0",
    base_url="https://api.deepseek.com"
)

debug = False  # 是否只处理一条
SAMPLE_SIZE = 2000  # 随机挑选的数据量
REWRITE_PROMPT = "Rewrite this in a human style (English)"  # 统一的改写指令

# ✅ 自动重试机制
@retry(wait=wait_random_exponential(min=1, max=60), stop=stop_after_attempt(6))
def GPT_self_prompt(prompt_str, content_to_be_detected):
    response = client.chat.completions.create(
        model="deepseek-chat",
        messages=[
            {"role": "user", "content": f"{prompt_str}: {content_to_be_detected}"}
        ],
        stream=False
    )
    spit_out = response.choices[0].message.content.strip()
    print(spit_out)
    return spit_out

# ✅ 加载AI生成文本并随机抽样
with open('AI.json', 'r', encoding='utf-8') as file:
    ai_texts = json.load(file)
    
sampled_ai_texts = random.sample(ai_texts, min(SAMPLE_SIZE, len(ai_texts)))  # 随机选2000条


In [4]:
# ✅ 主函数：用统一指令改写文本
def rewrite_to_human_style(input_texts):
    all_data = []
    for cc, text in enumerate(input_texts):
        print(f"Processing {cc + 1}/{len(input_texts)}")
        tmp_dict = {'original_ai_text': text}
        
        try:
            # 使用统一的人类风格改写指令
            tmp_dict['human_style_rewrite'] = GPT_self_prompt(REWRITE_PROMPT, text)
        except Exception as e:
            print(f"❌ Error at index {cc}: {e}")
            tmp_dict['human_style_rewrite'] = "ERROR"
        
        all_data.append(tmp_dict)
        if debug:
            break

    return all_data

# ✅ 处理AI文本改写
ai_rewritten = rewrite_to_human_style(sampled_ai_texts)

# ✅ 保存结果
with open('ai_rewritten_in_human_style.json', 'w', encoding='utf-8') as file:
    json.dump(ai_rewritten, file, indent=4, ensure_ascii=False)

print(f"完成！已处理 {len(ai_rewritten)} 条AI生成文本的改写。")

Processing 1/2000
Here’s a more natural and human-sounding rewrite of your text:  

---  

**Honesty is one of the most valuable qualities a person can have.** It’s especially important to be truthful with close friends, family, and—above all—ourselves. Honesty builds trust, deepens understanding, and fosters compassion. When we’re open with the people we care about, we show them that their place in our lives matters and that we’re comfortable being genuine around them. It also proves that they can rely on us to speak the truth.  

Honesty is just as crucial for our personal growth. It’s easy to get tangled in deception, whether by outright lying or by leaving out important truths. But when we’re honest with ourselves, we avoid getting lost in our own illusions. Only by confronting reality, no matter how hard it may be, can we truly learn and move forward.  

Most importantly, honesty is the key to lasting happiness. We should never feel pressured to lie or hide parts of ourselves just

Here’s a more natural, human-style rewrite of your text:  

---  

**Distance learning has taken off in a big way over the last few years.** Thanks to advances in technology and the internet, it’s now easier than ever to learn from anywhere in the world. For some students, the flexibility and convenience of studying from home is a game-changer. But for others, staying on track without the structure of a traditional classroom can be tough—especially when it comes to time management and motivation.  

**One of the biggest perks of distance learning? Freedom.** Students can work through their courses at their own pace, fitting study time around jobs, family, or other commitments. Plus, skipping the daily commute to campus means saving both time and money—a win for busy schedules and tight budgets.  

**That said, learning from home isn’t always smooth sailing.** Without set class times, some students struggle to stay disciplined, putting things off until the last minute. It’s easy to fall

**Why Libraries Still Matter in the Digital Age**  

For centuries, libraries have been the heart of communities—places where anyone, regardless of age or background, could find knowledge, stories, and connection. But now, with so much information just a click away, some wonder: *Do we still need libraries?* The answer is a resounding *yes.* Far from being outdated, libraries have adapted and thrived, proving just how essential they remain in our fast-changing world.  

### **1. Free Access to Reliable Information (No Wi-Fi Required)**  

Sure, the internet is full of information—but not everyone has a computer, reliable internet, or the skills to tell fact from fiction. Libraries level the playing field by offering free, well-researched books, articles, and databases in a welcoming space. Unlike the wild west of Google, libraries provide *curated* resources, saving people from drowning in misinformation. Whether you're researching a school project, learning a new skill, or just explor

Here’s a polished, human-written version of your letter with corrected grammar, clarity, and a natural tone:  

---  

**Senator [Name],**  

I’m writing to you as a concerned citizen about the ongoing debate surrounding the future of the Electoral College. As a representative of our shared values in government, I trust you deeply value the democratic principles that guide our nation. There are compelling arguments both for and against the Electoral College, and it’s on these points that I base my appeal.  

The Electoral College, as established in the Constitution, was designed as a compromise between a direct popular vote and congressional election of the president (Source: Office of the Federal Register). It was created to ensure states—both large and small—have a meaningful voice in presidential elections. According to Judge Richard A. Posner, the Electoral College provides certainty in outcomes, ensures the president has broad regional appeal, focuses campaigns on competitive stat

Here’s a more natural and human-like rewrite of your text:  

---  

### The Case for Using Fewer Cars  

As cities grow and urban areas become more crowded, it’s worth thinking about the benefits of cutting back on car use. Cars are a major contributor to pollution, traffic jams, and urban sprawl. Reducing our reliance on them could mean cleaner air, quieter streets, and more pleasant cities to live in.  

#### **Better Air Quality**  
Cars pump out harmful gases like carbon monoxide and nitrogen oxides, which create smog and acid rain. These pollutants are linked to serious health issues—respiratory diseases, heart problems, and even cancer. By driving less, we can help clear the air and protect our health.  

#### **Less Noise Pollution**  
The constant hum of traffic isn’t just annoying—it can disrupt sleep, make it harder to concentrate, and even raise stress levels. Fewer cars on the road would mean quieter neighborhoods and a more peaceful environment.  

#### **Less Traffic and

...

**A More Human-Style Rewrite:**  

The article *"The Challenge of Exploring Venus"* makes a strong case for why we should turn our attention to Earth’s scorching, toxic neighbor—despite the immense difficulties of doing so. The author builds a convincing argument by focusing on the exciting scientific discoveries we might uncover and the sheer thrill of solving Venus’s many mysteries.  

One of the most compelling points is the idea that Venus could hold clues about Earth’s past—and maybe even life. The author suggests that Venus might have once looked a lot like our own planet, with oceans, mountains, and perhaps even living organisms. If true, studying Venus could help us understand how Earth evolved and whether life exists beyond our world. The article also touches on the creative solutions scientists are considering, like floating blimp-like probes that could safely observe Venus from above its deadly surface. These details make a solid case for why exploring Venus is worth the ris

**Self-Driving Cars: Why We Need Them in the Future**  

Self-driving cars have sparked debates among people of all ages, backgrounds, and professions. While some are excited about the idea, others worry about the risks. Despite the challenges, I believe autonomous vehicles are a must for our future—and here’s why.  

First and foremost, driverless cars could drastically reduce accidents caused by human error. The National Highway Traffic Safety Administration reports that **94% of crashes** happen because of mistakes made by drivers. Self-driving cars, equipped with advanced sensors, cameras, and AI, can detect obstacles and react faster than humans, making roads much safer.  

Beyond safety, these cars could also **cut down traffic jams**. Using smart algorithms and real-time communication, autonomous vehicles can coordinate with each other, choosing the most efficient routes. This means less time stuck in traffic, lower fuel consumption, and a greener transportation system overall. 

**The Secret to Success? Taking Risks and Trying New Things**  

For as long as anyone can remember, people have chased after success—but what does it really take to achieve it? Some say it’s all about natural talent, while others swear by hard work and persistence. But here’s the truth: the most successful people don’t just stick to what they know. They push boundaries, take chances, and embrace the unknown. In this essay, I’ll explain why I believe stepping outside your comfort zone is the key to success, backed by real-world examples.  

### **Growth Happens Outside Your Comfort Zone**  
If you only do what you’re already good at, you’ll never grow. True success comes from facing challenges, learning new skills, and adapting to change. Think about an entrepreneur who clings to the same old business strategy—sooner or later, they’ll be left behind. But those who take risks? They discover new opportunities. A great example is Netflix, which started as a DVD rental service. Instead of 

Here’s a more natural, human-sounding rewrite of your text:  

---  

**Distance learning has become increasingly popular in recent years, opening doors for students from all walks of life.** Unlike traditional college settings, it lets people continue their education while juggling full-time jobs or family responsibilities. Plus, it’s often far more affordable than on-campus tuition—a game-changer for those without financial support.  

**For older students looking to finish or advance their education—whether they took a break due to life circumstances or never had the chance—distance learning offers a flexible path forward.** They can study at their own pace, fitting coursework around their schedule. And with online resources and instructors just a click away, location is no longer a barrier to learning.  

**At its core, distance learning is a lifeline—especially for parents, those without strong support systems, or students in underserved communities.** It breaks down financial and

Here’s a more natural and polished version of your text in human-style English:  

---  

I strongly believe we should transition from fossil fuels to renewable energy as soon as possible. Here’s why:  

First, fossil fuels are a finite resource—meaning they’ll eventually run out. Since we’ll have to switch to alternative energy sources anyway, why not start now? On top of that, fossil fuels are a major driver of climate change, which is already causing devastating effects on our planet. Shifting to renewable energy like solar and wind power would drastically cut carbon emissions and help fight global warming.  

Another big reason to make the switch is that renewable energy is becoming more affordable. Over the past decade, the cost of solar and wind power has dropped significantly, making it a smart financial choice for both households and businesses. This means we can reduce our dependence on fossil fuels while actually saving money.  

Renewable energy is also getting more efficien

In [5]:
#获取未被选中的文本
remaining_ai = [text for text in ai_texts if text not in sampled_ai_texts]
# ✅ 保存结果
with open('remaining_ai.json', 'w', encoding='utf-8') as file:
    json.dump(remaining_ai, file, indent=4, ensure_ascii=False)
#不能再运行了，否则sampled_ai_texts将变了

NameError: name 'sampled_ai_texts' is not defined

In [6]:
import json

# 加载 ai_rewritten_in_human_style.json
with open('remaining_ai.json', 'r', encoding='utf-8') as f:
    ai_rewritten = json.load(f)

# 加载 human.json
with open('ai_rewritten_in_human_style.json', 'r', encoding='utf-8') as f:
    human_texts = json.load(f)

# 打印数量
print("remaining_ai.json 中的总数:", len(ai_rewritten))
print("ai_rewritten_in_human_style.json 中的总数:", len(human_texts))


remaining_ai.json 中的总数: 179438
ai_rewritten_in_human_style.json 中的总数: 2000


In [30]:
import json
import random

# 读取 remaining_ai.json
with open("remaining_ai.json", "r", encoding="utf-8") as f:
    remaining_ai = json.load(f)

SAMPLE_SIZE=2000
sampled_remaining_ai = random.sample(remaining_ai, min(SAMPLE_SIZE, len(remaining_ai)))  # 随机选2000条

# 读取 ai_rewritten_in_human_style.json
with open("ai_rewritten_in_human_style.json", "r", encoding="utf-8") as f:
    ai_rewritten = json.load(f)
rewritten_texts = [item['human_style_rewrite'] for item in ai_rewritten if isinstance(item, dict) and 'human_style_rewrite' in item]
ai_rewritten = rewritten_texts#字典转化为字符

# 合并两个列表
combined_data = sampled_remaining_ai + ai_rewritten

# 保存为新文件 combined_ai_data.json
with open("combined_ai_data.json", "w", encoding="utf-8") as f:
    json.dump(combined_data, f, ensure_ascii=False, indent=2)

print(f"合并完成，共 {len(combined_data)} 条数据。")
#2000条attack，2000条未attack

合并完成，共 4000 条数据。


In [31]:
import json
import csv

# 1. 读取 combined_ai_data.json
with open("combined_ai_data.json", "r", encoding="utf-8") as f:
    ai_data = json.load(f)

# 每条加上 label = 'ai'
ai_labeled = [{"text": text, "label": "1"} for text in ai_data if isinstance(text, str)]

# 2. 读取 human.json
with open("human.json", "r", encoding="utf-8") as f:
    human_data = json.load(f)

SAMPLE_SIZE=8000
sampled_human_data = random.sample(human_data, min(SAMPLE_SIZE, len(human_data)))  # 随机选8000条

# 每条加上 label = 'human'
human_labeled = [{"text": text, "label": "0"} for text in sampled_human_data if isinstance(text, str)]

# 3. 合并
final_data = ai_labeled + human_labeled

# 4. 写入 CSV 文件
with open("attacked_ai_human.csv", "w", newline="", encoding="utf-8") as f:
    writer = csv.DictWriter(f, fieldnames=["text", "label"])
    writer.writeheader()
    writer.writerows(final_data)

print(f"CSV 写入完成，合计 {len(final_data)} 条数据。")
data1 = pd.read_csv('./attacked_ai_human.csv')
data1#4000AI,8000human

CSV 写入完成，合计 12000 条数据。


text  label
0      There is To right or wrote answer whet it come...      1
1      There are a variety of opinions on what the pr...      1
2      Title: The Future of Transportation: Driverles...      1
3      Visiting a museum is a great Opportunity Te le...      1
4      Introduction:\n\nHave you ever dreamed of trav...      1
...                                                  ...    ...
11995  Asking more than one person for advice can be ...      0
11996  Door Principle,\n\nI think that to should Beau...      0
11997  Dear state senator,\n\nI wish to inform you ab...      0
11998  Facial Action Coding System could potentially ...      0
11999  Driverless cars may be very interesting and CC...      0

[12000 rows x 2 columns]